In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import os
import sdv
from sdv.evaluation.single_table import evaluate_quality
from sdv.single_table import CTGANSynthesizer
from sdv.single_table import TVAESynthesizer
from sdv.metadata import SingleTableMetadata
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split
from xgboost import XGBRegressor
from sklearn.pipeline import Pipeline
from sklearn.model_selection import KFold, cross_validate
from sklearn.base import clone
from sklearn.metrics import r2_score, mean_squared_error
from sklearn.metrics import mean_absolute_error
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import LinearRegression
import os
from catboost import CatBoostRegressor
from pytorch_tabnet.tab_model import TabNetRegressor
from sklearn.neural_network import MLPRegressor
import keras
from keras import layers
from keras import models
import torch
from sklearn.decomposition import PCA

In [2]:
# Global variable
CURR_ACTIVITY = "mmo"
CURR_MUSCLE = "ta_r"
CURR_TYPE = "intensity"

In [3]:
# Read the data
data_sheet = pd.read_excel("Data sheet compile cleaned 17.8.23.xlsx")
data_sheet = data_sheet[["Ethnicity","Age",
                         "Gender", "Height (cm)",
                         "Weight (kg)", "BMI",
                         "Clicking", "Lockout",
                         "Jaw pain (in last 2 years)",
                         "Jaw Injuries", "Jaw clenching",
                         "Bruxism", "Sleep apnoea/snoring",
                         "nail or object biting",
                         "Dry/ sticky mouth", "chapped lips",
                         "increased thirst", "dysphagia",
                         "Dental filling in 2 years",
                         "RCTs/crowns in 2 years",
                         "3rd molars extracted",
                         "Orthodontic treatment",
                         "blocked nose", "Lisp",
                         "Stammering", "Vit D deficiency",
                         "Recurrent sinus infections",
                         "Asthma",
                         "Endocrine modifiers (Diabetes, PCOS, Ca Breast)",
                         "Hypertension or high cholesterol",
                         "Inflammatory disorders (arthritis or eczyma)",
                         "Mental health modifiers (stress, depression, anxiety, ADHD)",
                         "Long term medication taken for condition",
                         "Sinus surgery (adenoid or septal)"]].copy()

data_two = pd.read_excel("Biopak data compiled final 1-70 v2.xlsx")

In [4]:
# Visualize the data
data_sheet.head()

Ethnicity  Age  Gender  Height (cm)  Weight (kg)        BMI Clicking  \
0  Caucasian   23    male        180.0         70.0  21.604938       No   
1      Asian   27    male        176.0         68.0  21.952479       No   
2      Asian   21  female        148.0         43.0  19.631118       No   
3  Caucasian   18  female        165.0         53.0  19.467401      Yes   
4  Caucasian   64  female        177.0         82.0  26.173833       no   

  Lockout Jaw pain (in last 2 years) Jaw Injuries  ... Stammering  \
0      No                        Yes           No  ...         No   
1      No                         No           No  ...         no   
2      No                         No           No  ...         no   
3     Yes                         No           No  ...        yes   
4      no                         no           no  ...         no   

  Vit D deficiency Recurrent sinus infections Asthma  \
0               No                        yes     no   
1               no                         no     no   
2               no                         no     no   
3              yes                        yes     no   
4              yes                         no     no   

  Endocrine modifiers (Diabetes, PCOS, Ca Breast)  \
0                                              no   
1                                              no   
2                                             yes   
3                                              no   
4                                             yes   

  Hypertension or high cholesterol  \
0                               no   
1                               no   
2                               no   
3                              yes   
4                               no   

  Inflammatory disorders (arthritis or eczyma)  \
0                                           no   
1                                           no   
2                                           no   
3                                           no   
4                                          yes   

  Mental health modifiers (stress, depression, anxiety, ADHD)  \
0                                                 no            
1                                                 no            
2                                                 no            
3                                                 no            
4                                                 no            

  Long term medication taken for condition Sinus surgery (adenoid or septal)  
0                                       no                                no  
1                                       no                                no  
2                                       no                                no  
3                                      yes                               yes  
4                                      yes                               yes  

[5 rows x 34 columns]

#### Data cleaning

In [5]:
data_sheet.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 70 entries, 0 to 69
Data columns (total 34 columns):
 #   Column                                                       Non-Null Count  Dtype  
---  ------                                                       --------------  -----  
 0   Ethnicity                                                    70 non-null     object 
 1   Age                                                          70 non-null     int64  
 2   Gender                                                       70 non-null     object 
 3   Height (cm)                                                  70 non-null     float64
 4   Weight (kg)                                                  70 non-null     float64
 5   BMI                                                          70 non-null     float64
 6   Clicking                                                     70 non-null     object 
 7   Lockout                                                      70 non-null     objec

In [6]:
# # Replacing NAs for numeric columns with 0s
# def replace_with_zeroes(column_name):
#     data_sheet[column_name] = \
#         data_sheet[column_name].fillna(0).copy()
    
# numeric_column_names = [
#     "VAS ongoing - discomfort (of 10)",
#     "Jaw injury when? (months)",
#     "last 3rd molar extracted (in months)",
#     "When were the other teeth extracted? (in months)",
#     "treatment duration (in months)",
#     "Treatment completed when? (in months)",
#     "surgery done when? (in months)"
#     ]

# for col_name in numeric_column_names:
#     replace_with_zeroes(col_name)

# # Replacing remaining NAs with "not_applicable"
# data_sheet.fillna("not_applicable", inplace=True)

In [7]:
# data_sheet.info()

In [8]:
# List of specific features/columns to select
selected_columns = [
    'Canine-canine maxilla',
    'Molar - molar maxilla ',
    'Arch perimeter maxilla',
    'Canine-canine mandible',
    'Molar - molar mandible',
    'Arch perimeter mandible',
    'Overbite',
    'Overjet ',
    'ROM vertical',
    'ROM MAP',
    'ROM Lateral left',
    'ROM Lateral right',
    'ROM Slant',
    'Habitual Head tilt degree',
    'Head tilting direction',
    'Soft tissue Lateral left',
    'Soft tissue Lateral right',
    'chewing left side vertical',
    'chewing left side protrusion',
    'chewing left side Lateral left',
    'chewing left side Lateral right',
    'chewing right side vertical',
    'chewing right side protrusion',
    'chewing right side Lateral left',
    'chewing right side Lateral right',
    'chewing normal side vertical',
    'chewing normal  protrusion',
    'chewing normal side Lateral left',
    'chewing normal side Lateral right',
    'EMG clench TA-R',
    'EMG clench TA-L',
    'EMG clench MM-R',
    'EMG clench MM-L',
    'EMG max TA-R',
    'EMG max TA-L',
    'EMG max MM-R',
    'EMG max MM-L',
    'JVA MMO left integral',
    'JVA MMO left Integral <300Hz',
    'JVA MMO left Integral >300Hz',
    'JVA MMO left Integral ratio',
    'JVA MMO left peak amplitude',
    'JVA MMO left peak frequency',
    'JVA MMO left median frequency',
    'JVA MMO right integral',
    'JVA MMO right Integral <300Hz',
    'JVA MMO right Integral >300Hz',
    'JVA MMO right Integral ratio',
    'JVA MMO right peak amplitude',
    'JVA MMO right peak frequency',
    'JVA MMO right median frequency',
    'JVA MLE left integral',
    'JVA MLE left Integral <300Hz',
    'JVA MLE left Integral >300Hz',
    'JVA MLE left Integral ratio',
    'JVA MLE left peak amplitude',
    'JVA MLE left peak frequency',
    'JVA MLE left median frequency',
    'JVA MLE right integral',
    'JVA MLE right Integral <300Hz',
    'JVA MLE right Integral >300Hz',
    'JVA MLE right Integral ratio',
    'JVA MLE right peak amplitude',
    'JVA MLE right peak frequency',
    'JVA MLE right median frequency',
    'JVA MAP left integral',
    'JVA MAP left Integral <300Hz',
    'JVA MAP left Integral >300Hz',
    'JVA MAP left Integral ratio',
    'JVA MAP left peak amplitude',
    'JVA MAP left peak frequency',
    'JVA MAP left median frequency',
    'JVA MAP right integral',
    'JVA MAP right Integral <300Hz',
    'JVA MAP right Integral >300Hz',
    'JVA MAP right Integral ratio',
    'JVA MAP right peak amplitude',
    'JVA MAP right peak frequency',
    'JVA MAP right median frequency',
    'Fricative vertical',
    'Fricative protrusion',
    'Fricative Lateral left',
    'Fricative Lateral right',
    'Sibilant vertical',
    'Sibilant protrusion',
    'Sibilant Lateral left',
    'Sibilant Lateral right',
    'TH phonetics vertical',
    'TH phonetics protrusion',
    'TH phonetics Lateral left',
    'TH phonetics Lateral right',
    'BP phonetics vertical',
    'BP phonetics protrusion',
    'BP phonetics Lateral left',
    'BP phonetics Lateral right',
    '60s vertical',
    '60s protrusion',
    '60s Lateral left',
    '60s Lateral right',
    'Freeway space'
]
data_two = data_two[selected_columns].copy()

In [9]:
def add_quotients(muscle, data):
    intensity_quotients = pd.read_csv(f"quotients/{muscle}/quotient_intensity.csv")
    duration_quotients = pd.read_csv(f"quotients/{muscle}/quotient_duration.csv")
    temp_data_intensity = intensity_quotients.copy()
    temp_data_duration = duration_quotients.copy()
    temp_data_intensity.columns = [f"{muscle}_intensity_" + name
                                for name in temp_data_intensity.columns]
    temp_data_duration.columns = [f"{muscle}_duration_" + name
                                for name in temp_data_duration.columns]
    
    indices_to_insert_nan = [1, 40, 42, 60]

    # Insert NaN values without replacing existing values
    for index in indices_to_insert_nan:
        temp_data_intensity = pd.concat([temp_data_intensity.iloc[:index],
                                        pd.DataFrame([[np.nan] * len(temp_data_intensity.columns)],
                                                    columns=temp_data_intensity.columns),
                                                    temp_data_intensity.iloc[index:]],
                                                    ignore_index=True).copy()
        temp_data_duration = pd.concat([temp_data_duration.iloc[:index],
                                        pd.DataFrame([[np.nan] * len(temp_data_duration.columns)],
                                                    columns=temp_data_duration.columns),
                                                    temp_data_duration.iloc[index:]],
                                                    ignore_index=True).copy()
        
    # Add quotients to JVA data
    new_data = pd.concat([data, temp_data_intensity], axis=1)
    new_data = pd.concat([new_data, temp_data_duration], axis=1)

    return new_data

In [10]:
# Form entire dataset
combined_dataset = pd.concat([data_sheet,
                              data_two], axis=1)

# Add quotients
for muscle in ["mmo", "mle", "map"]:
    combined_dataset = add_quotients(muscle,
                                     combined_dataset).copy()
    
# Drop rows with NAs
combined_dataset.dropna(inplace=True)


In [11]:
# Function to remove features with 0 variance (constant value features)
def get_const_value_features_to_drop(df):
    return [e for e in df.columns if df[e].nunique() == 1]

features_to_drop = \
    get_const_value_features_to_drop(combined_dataset)
combined_dataset.drop(columns=features_to_drop, 
                      inplace=True)

# turn all categorical values to lower case for consistency
# Convert all entries to lowercase
combined_dataset = \
    combined_dataset.applymap(
        lambda x: x.lower() if isinstance(x, str) else x).copy()

# Remove all leading and trailing whitespaces
combined_dataset = \
    combined_dataset.applymap(
        lambda x: x.strip() if isinstance(x, str) else x).copy()

/var/folders/d7/ws_j0w7s5fddwxs6dv1374lw0000gn/T/ipykernel_42870/4006963973.py:13: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  combined_dataset.applymap(
/var/folders/d7/ws_j0w7s5fddwxs6dv1374lw0000gn/T/ipykernel_42870/4006963973.py:18: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  combined_dataset.applymap(


In [12]:
combined_dataset.info()

<class 'pandas.core.frame.DataFrame'>
Index: 66 entries, 0 to 69
Columns: 170 entries, Ethnicity to map_duration_da_l
dtypes: float64(126), int64(14), object(30)
memory usage: 88.2+ KB


In [13]:
# Select only categorical features
categorical_df = combined_dataset.select_dtypes(include='object').copy()
categorical_columns = categorical_df.columns

In [14]:
for column in categorical_columns:
    print(categorical_df[column].unique())

['caucasian' 'asian' 'indian' 'hispanic']
['male' 'female']
['no' 'yes']
['no' 'yes']
['yes' 'no']
['no' 'yes']
['yes' 'no']
['yes' 'no']
['yes' 'no']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['yes' 'no']
['no' 'yes']
['no' 'yes']
['yes' 'no']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['left' 'straight' 'right' 'righht']


In [15]:
# Fix last categorical column (convert righht to right)
combined_dataset[categorical_columns[-1]] = \
    combined_dataset[categorical_columns[-1]].map(
        lambda x: "right" if x == "righht" else x).copy()

In [16]:
# Select only categorical features
categorical_df = combined_dataset.select_dtypes(include='object').copy()
categorical_columns = categorical_df.columns

# Verify all categorical columns again
for column in categorical_columns:
    print(categorical_df[column].unique())

['caucasian' 'asian' 'indian' 'hispanic']
['male' 'female']
['no' 'yes']
['no' 'yes']
['yes' 'no']
['no' 'yes']
['yes' 'no']
['yes' 'no']
['yes' 'no']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['yes' 'no']
['no' 'yes']
['no' 'yes']
['yes' 'no']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['no' 'yes']
['left' 'straight' 'right']


In [17]:
# Remove participant with an ethnicity of hispanic
combined_dataset['Ethnicity'] = combined_dataset['Ethnicity'].map(
    lambda x: np.nan if x == "hispanic" else x)
combined_dataset.dropna(inplace=True)

In [61]:
def tune_tvae(features_ta_r_imputed_df, metadata):
    # Tuning a variational autoencoder
    tvae_scores = []
    embedding_dims = [128, 256]
    compress_dims = [128, 256]
    decompress_dims = [128, 256]

    for embedding_dim in embedding_dims:
        for compress_dim in compress_dims:
            for decompress_dim in decompress_dims:
                # Creating a Variational Autoencoder synthesizer
                tvae_synthesizer = TVAESynthesizer(metadata,
                                                embedding_dim=embedding_dim,
                                                compress_dims=(compress_dim,compress_dim),
                                                decompress_dims=(decompress_dim,decompress_dim),
                                                epochs=500)
                
                # Fitting the model
                tvae_synthesizer.fit(features_ta_r_imputed_df)
                
                # Generating synthetic data
                synthetic_data = tvae_synthesizer.sample(num_rows=200)

                # Evaluating synthetic data
                quality_report = evaluate_quality(
                    features_ta_r_imputed_df,
                    synthetic_data,
                    metadata,
                    verbose=False
                )

                tvae_scores.append((quality_report.get_score(), tvae_synthesizer))

    return tvae_scores

def tune_ctgan(features_ta_r_imputed_df, metadata):
    # Tuning a ctgan
    ctgan_scores = []
    embedding_dims = [256, 512]
    generator_dims = [256, 512]
    discriminator_dims = [128, 256]

    for embedding_dim in embedding_dims:
        for generator_dim in generator_dims:
            for discriminator_dim in discriminator_dims:
                # Creating a ctgan synthesizer
                ctgan_synthesizer = CTGANSynthesizer(metadata,
                                                    embedding_dim=embedding_dim,
                                                    generator_dim=(generator_dim,generator_dim),
                                                    discriminator_dim=(discriminator_dim,discriminator_dim),
                                                    epochs=500)
                
                # Fitting the model
                ctgan_synthesizer.fit(features_ta_r_imputed_df)
                
                # Generating synthetic data
                synthetic_data = ctgan_synthesizer.sample(num_rows=200)

                # Evaluating synthetic data
                quality_report = evaluate_quality(
                    features_ta_r_imputed_df,
                    synthetic_data,
                    metadata,
                    verbose=False
                )

                ctgan_scores.append((quality_report.get_score(), ctgan_synthesizer))

    return ctgan_scores

def run_augmentation_pipeline_tvae(features_ta_r_imputed_df):

    # Creating metadata object to get metadata about the original dataset of extracted features
    metadata = SingleTableMetadata()
    metadata.detect_from_dataframe(data=features_ta_r_imputed_df)

    # Get tvae and tuning results
    tvae_scores = tune_tvae(features_ta_r_imputed_df, metadata)

    # Return scores
    return tvae_scores

def run_augmentation_pipeline_ctgan(features_ta_r_imputed_df):

    # Creating metadata object to get metadata about the original dataset of extracted features
    metadata = SingleTableMetadata()
    metadata.detect_from_dataframe(data=features_ta_r_imputed_df)

    # Get ctgan tuning results
    ctgan_scores = tune_ctgan(features_ta_r_imputed_df, metadata)

    # Return scores
    return ctgan_scores

In [62]:
# Get TVAE scores
tvae_scores = run_augmentation_pipeline_tvae(combined_dataset)

C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\rdt\transformers\numerical.py:112: UserWarning: No rounding scheme detected for column 'BMI'. Data will not be rounded.
  warnings.warn(
C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\rdt\transformers\numerical.py:112: UserWarning: No rounding scheme detected for column 'BMI'. Data will not be rounded.
  warnings.warn(
C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\rdt\transformers\numerical.py:112: UserWarning: No rounding scheme detected for column 'BMI'. Data will not be rounded.
  warnings.warn(
C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\rdt\transformers\numerical.py:112: UserWarning: No rounding scheme detected for column 'BMI'. Data will not be rounded.
  warnings.warn(
C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\rdt\transformers\numerical.py:112: UserWarning: No rounding scheme detected for column 'BMI'. Data will not be rounded.
  warnings.warn(
C:\Us

In [63]:
# Get CTGAN scores
ctgan_scores = run_augmentation_pipeline_ctgan(combined_dataset)

C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\rdt\transformers\numerical.py:112: UserWarning: No rounding scheme detected for column 'BMI'. Data will not be rounded.
  warnings.warn(
C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\rdt\transformers\numerical.py:112: UserWarning: No rounding scheme detected for column 'BMI'. Data will not be rounded.
  warnings.warn(
C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\rdt\transformers\numerical.py:112: UserWarning: No rounding scheme detected for column 'BMI'. Data will not be rounded.
  warnings.warn(
C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\rdt\transformers\numerical.py:112: UserWarning: No rounding scheme detected for column 'BMI'. Data will not be rounded.
  warnings.warn(
C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\rdt\transformers\numerical.py:112: UserWarning: No rounding scheme detected for column 'BMI'. Data will not be rounded.
  warnings.warn(
C:\Us

In [64]:
# Creating a dataframe of tuning results for all
results = pd.DataFrame({
    "TVAE": sorted([each[0] for each in tvae_scores], reverse=True),
    "CTGAN": sorted([each[0] for each in ctgan_scores], reverse=True),
})
results

TVAE     CTGAN
0  0.673781  0.658483
1  0.673242  0.651170
2  0.671712  0.648258
3  0.660732  0.643133
4  0.656798  0.613119
5  0.654360  0.605527
6  0.652059  0.596353
7  0.641268  0.593590

In [65]:
# obtaining the best model
best_tvae = sorted(tvae_scores, reverse=True)[0]

# Save best models
path = "best_models/"
if not os.path.exists(path):  
    os.makedirs(path)
best_tvae[1].save(
    filepath = path + "/" + f"tvae.pkl"
)

In [77]:
# Loading the synthesizer
path = "best_models/"
best_synthesizer = TVAESynthesizer.load(
    filepath = path + "/" + f"tvae.pkl"
)

# Generating 2000 synthetic observations using the trained model
synthetic_data = best_synthesizer.sample(
    num_rows=5000, batch_size=100)

Sampling rows: 100%|██████████| 15000/15000 [00:54<00:00, 275.84it/s]


In [64]:
synthetic_data.to_csv("synthetic_data_5000.csv", index=False)

In [158]:
combined_dataset.to_csv("original_data_5000.csv", index=False)

In [ ]:
synthetic_data = pd.read_csv("synthetic_data.csv")
combined_dataset = pd.read_csv("combined_dataset.csv")

#### Start from here if you want to use saved data

In [78]:
# Obtain predictor and response variables
y_train = synthetic_data["Freeway space"].copy()
y_test = combined_dataset["Freeway space"].copy()
X_train = synthetic_data.drop(columns=["Freeway space"])
X_test = combined_dataset.drop(columns=["Freeway space"])

#### Preprocessing

In [79]:
# Separating the categorical and continuous variables
train_categorical = X_train.select_dtypes(include='object').copy()
test_categorical = X_test.select_dtypes(include='object').copy()
train_numeric = X_train.drop(columns=train_categorical.columns).copy()
test_numeric = X_test.drop(columns=test_categorical.columns).copy()

# Scaling the numeric data
scaler = StandardScaler()
train_numeric_scaled = scaler.fit_transform(train_numeric)
test_numeric_scaled = scaler.transform(test_numeric)

# One hot encoding the categorical data
train_categorical_encoded = pd.get_dummies(
    train_categorical, dtype=int
)
test_categorical_encoded = pd.get_dummies(
    test_categorical, dtype=int
)

# Combining to form final dataset
X_train_final = np.concatenate([train_numeric_scaled,
                                train_categorical_encoded],
                                axis=1)
X_test_final = np.concatenate([test_numeric_scaled,
                               test_categorical_encoded],
                               axis=1)

In [80]:
# Create a separate set of data for CatBoost
X_train_cb = np.concatenate([train_numeric_scaled,
                             train_categorical.values],
                             axis=1)
X_test_cb = np.concatenate([test_numeric_scaled,
                            test_categorical.values],
                            axis=1)

#### Modelling

In [26]:
def get_lr_results(X_train, y_train):
    scores_lr = []
    # Create a CV instance
    cv_lr = KFold(n_splits=5, shuffle=True, random_state=42)
    for train, val in cv_lr.split(X_train, y_train):
        X_train_temp = X_train[train]
        X_val_temp = X_train[val]
        y_train_temp = y_train.values[train]
        y_val_temp = y_train.values[val]

        # Define model
        lr_model = LinearRegression()
        lr_model.fit(X_train_temp, y_train_temp)

        # Predictions
        predictions_train = lr_model.predict(X_train_temp)
        predictions_val = lr_model.predict(X_val_temp)

        train_rmse = np.sqrt(mean_squared_error(y_train_temp,
                                                predictions_train))
        val_rmse = np.sqrt(mean_squared_error(y_val_temp,
                                            predictions_val))
        scores_lr.append((val_rmse, train_rmse))

    # Compute average scores
    avg_val_rmse_lr = np.sum([each[0]
                             for each in scores_lr]) / len(scores_lr)
    avg_train_rmse_lr = np.sum([each[1]
                               for each in scores_lr]) / len(scores_lr)
    
    # Final fitted model
    final_lr = LinearRegression()
    final_lr.fit(X_train, y_train)

    return ((avg_train_rmse_lr,
             avg_val_rmse_lr),
             final_lr)

In [27]:
"""
The following function was taken from
https://xgboost.readthedocs.io/en/stable/python/sklearn_estimator.html
"""
def fit_and_score(estimator, X_train, X_test, y_train, y_test):
    """Fit the estimator on the train set and score it on both sets"""
    estimator.fit(X_train, y_train,
                  eval_set=[(X_test, y_test)], verbose=False)
    predictions_train = estimator.predict(X_train)
    predictions_test = estimator.predict(X_test)
    train_score = np.sqrt(mean_squared_error(y_train,
                                             predictions_train))
    test_score = np.sqrt(mean_squared_error(y_test,
                                            predictions_test))
    return estimator, train_score, test_score

def get_catboost_results(X_train, y_train,
                         categorical_indices):
    model = CatBoostRegressor(early_stopping_rounds=10,
                              task_type="GPU",
                              cat_features=categorical_indices)
    params = {
        'depth':range(3,6,2),
        'iterations':[100,500,1000],
        'learning_rate':[0.001,0.01,0.03,0.1], 
        'l2_leaf_reg': [1, 3, 5, 7],
    }
    results = model.grid_search(params,
                                X=X_train,
                                y=y_train,
                                cv=5,
                                refit=True,
                                partition_random_seed=42)
    
    # Refit using best params to create best model
    best_params = results["params"]
    best_params["early_stopping_rounds"] = None
    best_model = CatBoostRegressor(**best_params,
                                   cat_features=categorical_indices)
    best_model.fit(X_train, y_train)

    # Get training and validation scores
    best_train_score = min(results['cv_results']['train-RMSE-mean'])
    best_val_score = min(results['cv_results']['test-RMSE-mean'])

    scores = {
        "Best Train RMSE": best_train_score,
        "Best Validation RMSE": best_val_score,
    }
    return scores, best_model

In [117]:
def get_xgboost_results(X_train, y_train):
    # Parameters to tune in the grid
    params_to_test = {
        'max_depth': range(3,10,2),
        'min_child_weight': range(1,6,2),
        'n_estimators': [100, 500, 1000],
        'learning_rate': [0.1, 0.01, 0.001]
    }

    # Performing gridSearch manually
    best_xgb_scores = None
    best_xgb_model = None
    curr_val_score = float('inf')
    for depth in params_to_test['max_depth']:
        for weight in params_to_test['min_child_weight']:
            for lr in params_to_test['learning_rate']:
                for estimator_count in params_to_test['n_estimators']:
                    # Create a CV instance
                    cv = KFold(n_splits=5, shuffle=True, random_state=42)

                    # XGBoost model
                    xgb_model = XGBRegressor(n_estimators=estimator_count, max_depth=depth,
                                             min_child_weight=weight, early_stopping_rounds=10,
                                             learning_rate=lr, tree_method="hist",
                                             device="cuda")
                    # curr_params = xgb_model.get_params()
                    # curr_params["tree_method"] = 'hist'
                    # curr_params["device"] = 'cuda'
                    # curr_params[""]
                    # xgb_model.set_params(**curr_params)

                    # Add cross validation results
                    total_train_score = 0
                    total_val_score = 0
                    for train, val in cv.split(X_train, y_train):
                        X_train_temp = X_train[train]
                        X_val_temp = X_train[val]
                        y_train_temp = y_train.values[train]
                        y_val_temp = y_train.values[val]

                        # # Transfer data to GPU
                        # X_train_temp_gpu = \
                        #     torch.tensor(X_train_temp).to('cuda:0')
                        # X_val_temp_gpu = \
                        #     torch.tensor(X_val_temp).to('cuda:0')
                        # y_train_temp_gpu = \
                        #     torch.tensor(y_train_temp).to('cuda:0')
                        # y_val_temp_gpu = \
                        #     torch.tensor(y_val_temp).to('cuda:0')

                        est, train_score, test_score = fit_and_score(
                            clone(xgb_model), X_train_temp,
                            X_val_temp, y_train_temp,
                            y_val_temp
                        )
                        total_train_score += train_score
                        total_val_score += test_score

                        avg_val_score = total_val_score / 5
                        if avg_val_score < curr_val_score:
                            curr_val_score = avg_val_score
                            best_xgb_scores = (total_train_score / 5, avg_val_score)
                            best_xgb_model = est

    # Determine best model (refitted)
    best_params = best_xgb_model.get_params()
    best_params["early_stopping_rounds"] = None
    best_model = XGBRegressor(**best_params)
    best_model.fit(X_train, y_train)
    return best_xgb_scores, best_model


In [29]:
def get_rf_results(X_train, y_train):
    params_to_test = {
        'max_depth': range(3,10,2),
        'n_estimators': [100, 500, 1000],
        'max_features': [1.0, 'sqrt', 'log2']
    }
    rf_grid = GridSearchCV(RandomForestRegressor(random_state=42),
                           params_to_test, cv=5,
                           scoring='neg_mean_squared_error',
                           return_train_score=True)

    # Best scores
    rf_grid.fit(X_train, y_train)
    rf_train_score = np.sqrt(
        -rf_grid.cv_results_['mean_train_score'][rf_grid.best_index_])
    rf_val_score = np.sqrt(-rf_grid.best_score_)

    # Best params
    best_params = rf_grid.best_params_
    best_model = RandomForestRegressor(**best_params)
    best_model.fit(X_train, y_train)

    return (rf_train_score, rf_val_score), best_model

In [100]:
def get_mlp_results(X_train, y_train):
    model = models.Sequential()
    model.add(layers.Dense(100, activation='relu', input_shape=(X_train.shape[1],)))
    model.add(layers.Dense(500, activation='relu'))
    model.add(layers.Dense(200, activation='relu'))
    model.add(layers.Dense(100, activation='relu'))
    model.add(layers.Dense(1)) # now using Sigmoid

    # We define a Callback
    callback = keras.callbacks.EarlyStopping(patience=50, monitor='loss')
    model.compile(loss='mean_squared_error',
                  optimizer='adam',
                  metrics=keras.metrics.RootMeanSquaredError(name='rmse'))

    history = model.fit(X_train, y_train,
                        validation_split=0.20,
                        batch_size=min([200, X_train.shape[0]]),
                        epochs=1000, callbacks=[callback])
    
    min_loss = float('inf')
    best_epoch = -1
    for i, each in enumerate(history.history["val_loss"]):
        if each < min_loss:
            min_loss = each
            best_epoch = i

    best_score = history.history["val_rmse"][best_epoch]
    best_loss = history.history["val_loss"][best_epoch]

    return (best_loss, best_score), model

In [101]:
def get_tabnet_results(X_train, y_train):
    # Create a CV instance
    reduced_X_train, X_val, reduced_y_train, y_val = \
        train_test_split(X_train, y_train, train_size=0.80)
    
    model = TabNetRegressor()
    model.fit(reduced_X_train,
              reduced_y_train,
              eval_metric=["rmse"],
              eval_set=[(X_val, y_val)],
              max_epochs=1000,
              patience=100)
    best_epoch = model.best_epoch
    best_loss = model.history.history['loss'][best_epoch]
    best_rmse = model.history.history['val_0_rmse'][best_epoch]
    return (best_loss, best_rmse), model

#### Running all models

In [97]:
# Linear regression
lr_results = get_lr_results(X_train_final, y_train)

In [90]:
# Catboost
cb_results = get_catboost_results(X_train_cb,
                                  y_train,
                                  categorical_indices=list(range(91,121)))

0:	learn: 1.8022377	test: 1.8146873	best: 1.8146873 (0)	total: 5.37ms	remaining: 531ms
1:	learn: 1.8007184	test: 1.8131751	best: 1.8131751 (1)	total: 10.4ms	remaining: 509ms
2:	learn: 1.7992101	test: 1.8116707	best: 1.8116707 (2)	total: 15.2ms	remaining: 490ms
3:	learn: 1.7976994	test: 1.8101641	best: 1.8101641 (3)	total: 20.1ms	remaining: 483ms
4:	learn: 1.7961930	test: 1.8086571	best: 1.8086571 (4)	total: 25.7ms	remaining: 489ms
5:	learn: 1.7946768	test: 1.8071390	best: 1.8071390 (5)	total: 30.6ms	remaining: 479ms
6:	learn: 1.7931715	test: 1.8056404	best: 1.8056404 (6)	total: 35.3ms	remaining: 469ms
7:	learn: 1.7916636	test: 1.8041370	best: 1.8041370 (7)	total: 41.1ms	remaining: 473ms
8:	learn: 1.7901650	test: 1.8026435	best: 1.8026435 (8)	total: 45.9ms	remaining: 464ms
9:	learn: 1.7886550	test: 1.8011413	best: 1.8011413 (9)	total: 50.9ms	remaining: 458ms
10:	learn: 1.7871582	test: 1.7996473	best: 1.7996473 (10)	total: 56.3ms	remaining: 456ms
11:	learn: 1.7856525	test: 1.7981409	best

In [115]:
X_train_final.shape

(15000, 154)

In [118]:
# XGBoost results
xgb_results = get_xgboost_results(X_train_final,
                                  y_train)

In [234]:
# Random forest results
rf_results = get_rf_results(X_train_final,
                            y_train)

In [102]:
mlp_results = get_mlp_results(X_train_final,
                              y_train)

Epoch 1/1000
60/60 [==============================] - 1s 4ms/step - loss: 0.6148 - rmse: 0.7841 - val_loss: 0.4381 - val_rmse: 0.6619
Epoch 2/1000
60/60 [==============================] - 0s 3ms/step - loss: 0.3839 - rmse: 0.6196 - val_loss: 0.4023 - val_rmse: 0.6343
Epoch 3/1000
60/60 [==============================] - 0s 3ms/step - loss: 0.3328 - rmse: 0.5769 - val_loss: 0.3706 - val_rmse: 0.6088
Epoch 4/1000
60/60 [==============================] - 0s 3ms/step - loss: 0.3023 - rmse: 0.5498 - val_loss: 0.3637 - val_rmse: 0.6030
Epoch 5/1000
60/60 [==============================] - 0s 3ms/step - loss: 0.2588 - rmse: 0.5087 - val_loss: 0.4034 - val_rmse: 0.6351
Epoch 6/1000
60/60 [==============================] - 0s 3ms/step - loss: 0.2295 - rmse: 0.4790 - val_loss: 0.3884 - val_rmse: 0.6232
Epoch 7/1000
60/60 [==============================] - 0s 3ms/step - loss: 0.1960 - rmse: 0.4427 - val_loss: 0.3906 - val_rmse: 0.6250
Epoch 8/1000
60/60 [==============================] - 0s 3ms/s

In [103]:
# Tabnet results
tabnet_results = get_tabnet_results(X_train_final,
                                    y_train.values.reshape(-1,1))

C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\pytorch_tabnet\abstract_model.py:82: UserWarning: Device used : cuda
  warnings.warn(f"Device used : {self.device}")


epoch 0  | loss: 1.66937 | val_0_rmse: 0.87336 |  0:00:00s
epoch 1  | loss: 0.69573 | val_0_rmse: 0.77474 |  0:00:00s
epoch 2  | loss: 0.57007 | val_0_rmse: 0.77805 |  0:00:01s
epoch 3  | loss: 0.54502 | val_0_rmse: 0.74582 |  0:00:01s
epoch 4  | loss: 0.52187 | val_0_rmse: 0.74216 |  0:00:01s
epoch 5  | loss: 0.51657 | val_0_rmse: 0.74054 |  0:00:01s
epoch 6  | loss: 0.51191 | val_0_rmse: 0.73338 |  0:00:02s
epoch 7  | loss: 0.5032  | val_0_rmse: 0.72866 |  0:00:02s
epoch 8  | loss: 0.50123 | val_0_rmse: 0.72075 |  0:00:02s
epoch 9  | loss: 0.49266 | val_0_rmse: 0.71944 |  0:00:03s
epoch 10 | loss: 0.5009  | val_0_rmse: 0.71549 |  0:00:03s
epoch 11 | loss: 0.48452 | val_0_rmse: 0.7153  |  0:00:03s
epoch 12 | loss: 0.49318 | val_0_rmse: 0.71488 |  0:00:04s
epoch 13 | loss: 0.48439 | val_0_rmse: 0.69915 |  0:00:04s
epoch 14 | loss: 0.47736 | val_0_rmse: 0.70185 |  0:00:04s
epoch 15 | loss: 0.47064 | val_0_rmse: 0.69591 |  0:00:05s
epoch 16 | loss: 0.47336 | val_0_rmse: 0.695   |  0:00:0

C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\pytorch_tabnet\callbacks.py:172: UserWarning: Best weights from best epoch are automatically used!
  warnings.warn(wrn_msg)


#### Results

In [251]:
# For non NN models
val_results = pd.DataFrame({
    "Train RMSE": [lr_results[0][0],
                   rf_results[0][0],
                   cb_results[0]["Best Train RMSE"],
                   xgb_results[0][0]],
    "Validation RMSE": [lr_results[0][1],
                        rf_results[0][1],
                        cb_results[0]["Best Validation RMSE"],
                        xgb_results[0][1]]
})
val_results.index = ["Linear Regression",
                     "Random Forest",
                     "Catboost Regressor",
                     "XGBoost Regressor"]

val_results

Train RMSE  Validation RMSE
Linear Regression     0.642810         0.668416
Random Forest         0.482931         0.677430
Catboost Regressor    0.505620         0.648949
XGBoost Regressor     0.044608         0.132050

### Repeating everything with only numeric variables

In [73]:
### Try different type of scaling
scaler_two = MinMaxScaler()
train_numeric_scaled_2 = scaler_two.fit_transform(train_numeric)
test_numeric_scaled_2 = scaler_two.transform(test_numeric)

In [135]:
xgb_results_numeric = get_xgboost_results(train_numeric_scaled, y_train)

In [136]:
xgb_results_numeric

((0.07808435641173518, 0.1288369793439547),
 XGBRegressor(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device='cuda', early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=5, max_leaves=None,
              min_child_weight=1, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=500, n_jobs=None,
              num_parallel_tree=None, random_state=None, ...))

In [72]:
tabnet_results_numeric = get_tabnet_results(train_numeric_scaled,
                                            y_train.values.reshape(-1,1))

C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\pytorch_tabnet\abstract_model.py:82: UserWarning: Device used : cuda
  warnings.warn(f"Device used : {self.device}")


epoch 0  | loss: 2.09753 | val_0_rmse: 1.17976 |  0:00:00s
epoch 1  | loss: 1.17371 | val_0_rmse: 0.96989 |  0:00:00s
epoch 2  | loss: 0.76868 | val_0_rmse: 0.90827 |  0:00:00s
epoch 3  | loss: 0.63967 | val_0_rmse: 0.80302 |  0:00:00s
epoch 4  | loss: 0.56484 | val_0_rmse: 0.80104 |  0:00:00s
epoch 5  | loss: 0.55049 | val_0_rmse: 0.75676 |  0:00:00s
epoch 6  | loss: 0.532   | val_0_rmse: 0.76786 |  0:00:01s
epoch 7  | loss: 0.54708 | val_0_rmse: 0.75282 |  0:00:01s
epoch 8  | loss: 0.52465 | val_0_rmse: 0.75478 |  0:00:01s
epoch 9  | loss: 0.515   | val_0_rmse: 0.74725 |  0:00:01s
epoch 10 | loss: 0.53123 | val_0_rmse: 0.745   |  0:00:01s
epoch 11 | loss: 0.51551 | val_0_rmse: 0.74267 |  0:00:01s
epoch 12 | loss: 0.52029 | val_0_rmse: 0.74476 |  0:00:02s
epoch 13 | loss: 0.52337 | val_0_rmse: 0.74732 |  0:00:02s
epoch 14 | loss: 0.50233 | val_0_rmse: 0.74168 |  0:00:02s
epoch 15 | loss: 0.50883 | val_0_rmse: 0.74448 |  0:00:02s
epoch 16 | loss: 0.50259 | val_0_rmse: 0.74189 |  0:00:0

C:\Users\tashr\AppData\Roaming\Python\Python310\site-packages\pytorch_tabnet\callbacks.py:172: UserWarning: Best weights from best epoch are automatically used!
  warnings.warn(wrn_msg)


In [140]:
mean_absolute_error(y_test,
                    tabnet_results[1].predict(X_test_final))

0.7422016241333702